### 1. Generating data...

In [1]:
from ecog2vec.data_generator import NeuralDataGenerator

In [2]:
# efc401 = NeuralDataGenerator('/NWB/EFC401', 'EFC401')
# efc401.bad_electrodes = [1,2,63,64,65,127,143,193,194,195,196,235,239,243,252,254,255,256]
# efc401.bad_electrodes = [x - 1 for x in efc401.bad_electrodes]
# efc401.good_electrodes = [x for x in efc401.good_electrodes if x not in efc401.bad_electrodes]

import random

efc400 = NeuralDataGenerator('/NWB/EFC400', 'EFC400')
efc400.bad_electrodes = [1, 2, 33, 50, 54, 64, 128, 129, 193, 194, 256]

available_numbers = [num for num in range(1, 257) if num not in efc400.bad_electrodes]
random_numbers = random.sample(available_numbers, 7)
efc400.bad_electrodes = efc400.bad_electrodes + random_numbers

efc400.bad_electrodes = [x - 1 for x in efc400.bad_electrodes]
efc400.good_electrodes = [x for x in efc400.good_electrodes if x not in efc400.bad_electrodes]

In [4]:
import os
# Save clipped data for training,
# save unclipped data to extract features from,
# save entire recording as chunks for training,
# save entire reocording to extract features from
parent_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs'

chopped_sentence_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/chopped_sentence'
sentence_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/sentence'
chopped_recording_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/chopped_recording'
full_recording_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/full_recording'

temp = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/400_pretrain_401'

for directory in [parent_dir, chopped_sentence_dir, sentence_dir, chopped_recording_dir, full_recording_dir]:
    os.makedirs(directory, exist_ok=True)
    print(f"Directory created or already exists: {directory}")

chunk_length = 200000

block_list = []

# 'write_raw_data', but really it's filtered to the high
# gamma range and the analytic amplitude is calculated
efc400.write_raw_data(
    # chopped_sentence_dir=chopped_sentence_dir,
    # sentence_dir=sentence_dir,
    full_recording_dir=temp,
    # chopped_recording_dir=chopped_recording_dir,
    chunk_length=chunk_length)

Directory created or already exists: /home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs
Directory created or already exists: /home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/chopped_sentence
Directory created or already exists: /home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/sentence
Directory created or already exists: /home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/chopped_recording
Directory created or already exists: /home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/full_recording


/home/bayuan/anaconda3/envs/ecog2txt/lib/python3.9/site-packages/hdmf/spec/namespace.py:531: UserWarning: Ignoring cached namespace 'hdmf-common' version 1.6.0 because version 1.8.0 is already loaded.
  warn("Ignoring cached namespace '%s' version %s because version %s is already loaded."
/home/bayuan/anaconda3/envs/ecog2txt/lib/python3.9/site-packages/hdmf/spec/namespace.py:531: UserWarning: Ignoring cached namespace 'hdmf-experimental' version 0.3.0 because version 0.5.0 is already loaded.
  warn("Ignoring cached namespace '%s' version %s because version %s is already loaded."
/home/bayuan/anaconda3/envs/ecog2txt/lib/python3.9/site-packages/hdmf/spec/namespace.py:531: UserWarning: Ignoring cached namespace 'hdmf-common' version 1.6.0 because version 1.8.0 is already loaded.
  warn("Ignoring cached namespace '%s' version %s because version %s is already loaded."
/home/bayuan/anaconda3/envs/ecog2txt/lib/python3.9/site-packages/hdmf/spec/namespace.py:531: UserWarning: Ignoring cached na

### 2. Train and extract `wav2vec` features

Split into test/valid and train.

Strides should downsample by ~30x; `wav2vec` takes 16kHz inputs and our raw data is at 3kHz

In [5]:
# Borrowed from facebookresearch/fairseq with minor modifications

!python3 /home/bayuan/Documents/fall23/fairseq/examples/wav2vec/wav2vec_manifest.py \
    /home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/chopped_recording \
  --dest /home/bayuan/Documents/fall23/ecog2vec/manifest \
  --ext wav \
  --valid-percent 0.1 \
  --seed 42

In [1]:
# Borrowed from facebookresearch/fairseq with minor modifications
# , (512, 4, 3), (512, 4, 2), (512, 1, 1)

!python3 -c 'import argparse; print(argparse.__file__)'
!python3 /home/bayuan/Documents/fall23/fairseq/train.py \
    /home/bayuan/Documents/fall23/ecog2vec/manifest \
  --save-dir /home/bayuan/Documents/fall23/ecog2vec/model \
  --num-workers 6 --fp16 --max-update 400000 --save-interval 1 --infonce --no-epoch-checkpoints \
  --arch wav2vec --task audio_pretraining --min-lr 1e-06 --stop-min-lr 1e-09 --optimizer adam --lr 0.0001 --lr-scheduler cosine \
  --conv-feature-layers "[(512, 8, 30)]" \
  --conv-aggregator-layers "[(512, 12, 1)]" \
  --skip-connections-agg --residual-scale 0.5 --log-compression --warmup-updates 500 --warmup-init-lr 1e-07 --num-negatives 10 \
  --max-sample-size 1500000 --skip-invalid-size-inputs-valid-test  --batch-size 10 --max-tokens 1500000000 \
  --tensorboard-logdir /home/bayuan/Documents/fall23/ecog2vec/runs --prediction-steps 12 --criterion wav2vec

/home/bayuan/anaconda3/envs/ecog2txt/lib/python3.9/argparse.py
2023-12-15 19:49:31.647011: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-15 19:49:31.647050: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-15 19:49:31.648220: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-15 19:49:31.653141: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compil

Extract $c$ embeddings.

extract sentence features


In [12]:
# Borrowed from facebookresearch/fairseq with minor modifications

import torch
import fairseq
# from scipy.io import wavfile
import os
import soundfile as sf
import numpy as np

cp_path = '/home/bayuan/Documents/fall23/ecog2vec/model/checkpoint_best.pt'#'/path/to/wav2vec.pt'
model, cfg, task = fairseq.checkpoint_utils.load_model_ensemble_and_task([cp_path])
model = model[0]
model.eval()

dir_path = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/sentence'
feature_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/latent_sentence'

for directory in [feature_dir]:
    os.makedirs(directory, exist_ok=True)
    print(f"Directory created or already exists: {directory}")

for file in os.listdir(dir_path):

    wav_path = str(os.path.join(dir_path, file))

    wav_input_16khz, sr = sf.read(wav_path, dtype='float64')
    # 
    wav_input_16khz = wav_input_16khz.T
    wav_input_16khz = wav_input_16khz.reshape(1, 238, -1)#wav_input_16khz[np.newaxis, :, :] # change to 256; 480

    wav_input_16khz = torch.from_numpy(wav_input_16khz).to(torch.float)
    # print(wav_input_16khz.shape)

    # print(sr, wav_input_16khz.shape)
    z = model.feature_extractor(wav_input_16khz)
    c = model.feature_aggregator(z)
    
    torch.save(c, f"/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/latent_sentence/{file}.pt")

2023-12-14 08:57:33.580196: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-14 08:57:33.580230: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-14 08:57:33.581126: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-14 08:57:33.585064: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-12-14 08:57:34.206194: W tensorflow/compiler/tf2

Directory created or already exists: /home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/latent_sentence


extract entire recording features

In [1]:
# Borrowed from facebookresearch/fairseq with minor modifications

import torch
import fairseq
# from scipy.io import wavfile
import os
import soundfile as sf
import numpy as np

cp_path = '/home/bayuan/Documents/fall23/ecog2vec/model/checkpoint_best.pt'#'/path/to/wav2vec.pt'
model, cfg, task = fairseq.checkpoint_utils.load_model_ensemble_and_task([cp_path])
model = model[0]
model.eval()

dir_path = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_inputs/400_pretrain_401'

for file in os.listdir(dir_path):

    wav_path = str(os.path.join(dir_path, file))

    wav_input_16khz, sr = sf.read(wav_path)
    print(type(wav_input_16khz))
    # 
    wav_input_16khz = wav_input_16khz.T
    wav_input_16khz = wav_input_16khz.reshape(1, 238, -1)#wav_input_16khz[np.newaxis, :, :] # change to 256; 480

    wav_input_16khz = torch.from_numpy(wav_input_16khz).to(torch.float)
    # print(wav_input_16khz.shape)

    # print(sr, wav_input_16khz.shape)
    z = model.feature_extractor(wav_input_16khz)
    c = model.feature_aggregator(z)
    
    torch.save(c, f"/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/400_pretrain_401/full/{file}.pt")

2023-12-16 12:48:05.312763: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-16 12:48:05.312795: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-16 12:48:05.313825: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-16 12:48:05.319410: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-12-16 12:48:05.872769: W tensorflow/compiler/tf2

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>


In [ ]:
# If the entire recording is extracted, this cell must be ran to split the recording into its 
# individual sentences.

import torch
import os
from pynwb import NWBHDF5IO
import numpy as np
import soundfile as sf
import pandas as pd

file_list = []
entire_recording_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/400_pretrain_401/full'
patient = 'EFC400'
nwb_file_dir = '/NWB/EFC400'
nwb_file_prefix = f'{patient}_B'
nwb_file_suffix = f'.wav.pt'

saved_latent_sentences_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/400_pretrain_401/sentence'

for file in os.listdir(entire_recording_dir):
    c_filepath = os.path.join(entire_recording_dir, file)
   
    c = torch.load(c_filepath).detach().numpy()[0]
    nwb_file = file.rstrip(nwb_file_suffix)
    
    nwb_path = os.path.join(nwb_file_dir, nwb_file)
    io = NWBHDF5IO(nwb_path, load_namespaces=True, mode='r')
    nwbfile = io.read()
    
    sr = 101.7
    
    starts = list(nwbfile.trials[:]['start_time'] * sr)
    stops = list(nwbfile.trials[:]['stop_time'] * sr)
    starts = [int(start) for start in starts]
    stops = [int(stop) for stop in stops]
    
    i = 0
    for start, stop in zip(starts, stops):
        speaking_segment = c[:,start:stop]
        torch.save(speaking_segment, f'{saved_latent_sentences_dir}/{nwb_file}_{i}.wav.pt')
        i = i + 1
    
# file_list

Let's look at the data


In [5]:
import torch
import matplotlib.pyplot as plt

# cc = torch.load('/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/latent_representations/EFC400/EFC400_B3.nwb_0.wav.pt')
c = torch.load('/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/latent_sentence/EFC400_B10.nwb_0.wav.pt')
cc = c# .detach().numpy()[0]

print(cc.shape)
# print(cc[6])

fig, ax = plt.subplots(3,3)

# print(len(cc[0]))
ax[0,0].plot(cc[0])
ax[0,1].plot(cc[1])
ax[0,2].plot(cc[2])
ax[1,0].plot(cc[3])
ax[1,1].plot(cc[4])
ax[1,2].plot(cc[5])
ax[2,0].plot(cc[6])
ax[2,1].plot(cc[7])
ax[2,2].plot(cc[8])

(512, 269)


### 3. Write to tf_records for `ecog2txt`

The following cell is for nwbfile checking only.

In [ ]:
from pynwb import NWBHDF5IO
import numpy as np
import soundfile as sf
import os
import pandas as pd
# EFC400
# 3, 23, 72 chablis
# 4, 28,  hispanic
# 38 8 mayan
# 61 19 plymouth
# 57 15 gremlins
# 46 14 synagogue
# 42 12 giraffes
# 40 10 puree
# 30 6 bungalow
# 
# 401
# 8, 
# 12 hyenas
# 17 illuminating
# 18 funding
# 20 brie
# 32 tycoons
# 34 spurious
# 4, 41, 57, 61, 66, 69, 73, 77, 83, 87,  innocence
# 6 penguisn

path = '/NWB/EFC401/EFC401_B4.nwb'
io = NWBHDF5IO(path, load_namespaces=True, mode='r')
nwbfile = io.read()
nwbfile
# nwbfile.trials[:] # ['transcription'][0]

In [ ]:
import tensorflow as tf
import os
from machine_learning.neural_networks import tf_helpers as tfh
import pdb

from pynwb import NWBHDF5IO
import numpy as np
import os
import torch
import soundfile as sf

# Creating a list of dictionaries of:
# 
# `ecog_sequence`: ECoG data, clipped to token(-sequence) length
# `text_sequence`: the corresponding text token(-sequence)
# `audio_sequence`: the corresponding audio (MFCC) token sequence (gonna set to)
# `phoneme_sequence`: ditto for phonemes--with repeats
#
# Then saving them as tf_records

def transcription_to_array(trial_t0, trial_tF, onset_times, offset_times, transcription, max_length, sampling_rate):
    
    # if the transcription is missing (e.g. for covert trials)
    if transcription is None:
        return np.full(max_length, 'pau', dtype='<U5')

    # get just the parts of transcript relevant to this trial
    trial_inds = (onset_times >= trial_t0) * (offset_times < trial_tF)
    transcript = np.array(transcription.description.split(' '))[trial_inds]
    onset_times = np.array(onset_times[trial_inds])
    offset_times = np.array(offset_times[trial_inds])

    # vectorized indexing
    sample_times = trial_t0 + np.arange(max_length)/sampling_rate
    indices = (
        (sample_times[None, :] >= onset_times[:, None]) *
        (sample_times[None, :] < offset_times[:, None])
    )

    # no more than one phoneme should be on at once...
    try:
        # print('exactly one phoneme:', np.all(np.sum(indices, 0) == 1))
        assert np.all(np.sum(indices, 0) < 2)
    except:
        pdb.set_trace()

    # ...but there can be locations with *zero* phonemes; assume 'pau' here
    transcript = np.insert(transcript, 0, 'pau')
    indices = np.sum(indices*(np.arange(1, len(transcript))[:, None]), 0)

    return transcript[indices]

def sentence_tokenize(token_list): # token_type = word_sequence
    tokenized_sentence = [
                (token.lower() + '_').encode('utf-8') for token in token_list
            ]
    return tokenized_sentence

def write_to_Protobuf(path, example_dicts):
    '''
    Collect the relevant ECoG data and then write to disk as a (google)
        protocol buffer.
    '''
    writer = tf.io.TFRecordWriter(
        path)
    for example_dict in example_dicts:
        feature_example = tfh.make_feature_example(example_dict)
        writer.write(feature_example.SerializeToString())
            
# sorting function for latent representation filenames
def custom_sort_key(filename):
    num_part = int(filename.split('nwb_')[1].split('.wav.pt')[0])
    return num_part

all_example_dict = []

patient = 'EFC400'            
blocks = [3, 23, 72]
        #[4, 41, 57, 61, 66, 69, 73, 77, 83, 87] # [3,4,6,8,10,12,14,15,19,23,28,30,38,40,42,46,57,61,72] # change this for what tf_record you're making
for block in blocks:
    tfrecord_path = f'/home/bayuan/Documents/fall23/ecog2vec/wav2vec_tfrecords/ecog2txt/word_sequence/400_pretrain_401/{patient}_B{block}.tfrecord'

    nwb_filepath = folder_path = f"/NWB/{patient}/{patient}_B{block}.nwb"
    io = NWBHDF5IO(nwb_filepath, load_namespaces=True, mode='r')
    nwbfile = io.read()
    
    ### GETTING LATENT REPRESENTATION PATHS ###
    c_vectors_dir = '/home/bayuan/Documents/fall23/ecog2vec/wav2vec_outputs/400_pretrain_401/sentence'
    prefix = f'{patient}_B{block}.nwb_' 

    c_file_path_list = []

    for filename in os.listdir(c_vectors_dir):
        if filename.startswith(prefix):
            c_file_path_list.append(os.path.join(c_vectors_dir, filename))
            
    c_file_path_list = sorted(c_file_path_list, key=custom_sort_key)
    print(c_file_path_list)
    ###########################################
    phoneme_transcriptions = nwbfile.processing['behavior'].data_interfaces['BehavioralEpochs'].interval_series #['phoneme transcription'].timestamps[:]

    token_type = 'word_sequence'

    max_seconds_dict = {
        'phoneme': 0.2,
        'word': 1.0,
        'word_sequence': 6.25,
        'word_piece_sequence': 6.25,
        'phoneme_sequence': 6.25,
        'trial': 6.25
    }

    if 'phoneme transcription' in phoneme_transcriptions:
        print(f'Phoneme transcription for block {block} exists.')
        phoneme_transcript = phoneme_transcriptions['phoneme transcription']
        phoneme_onset_times = phoneme_transcript.timestamps[
            phoneme_transcript.data[()] == 1]
        phoneme_offset_times = phoneme_transcript.timestamps[
            phoneme_transcript.data[()] == -1]
    else:
        phoneme_transcript = None
        phoneme_onset_times = None
        phoneme_offset_times = None

    example_dicts = []

    makin_sr = 200 # screw it, actually just pass in c_sr everywhere
    c_sr = 101 # 399# 18

    for index, trial in enumerate(nwbfile.trials):
        
        # ECOG (C) SEQUENCE
        c_filepath = c_file_path_list[index]
        c = torch.load(c_filepath) #.detach().numpy()[0] # [1, nchannel, samples]
        # c = c.reshape(512,-1) # [nchannel, samples]
        c = c.T # [samples, nchannel]
    
        print(c.shape)
        nsamples = c.shape[0]
        
        # TEXT SEQUENCE
        speech_string = trial['transcription'].values[0]
        text_sequence = sentence_tokenize(speech_string.split(' ')) # , 'text_sequence')
        
        # AUDIO SEQUENCE    
        audio_sequence = []
        
        # PHONEME SEQUENCE
        t0 = float(trial.iloc[0].start_time)
        tF = float(trial.iloc[0].stop_time)
    
        i0 = np.rint(c_sr*t0).astype(int)
        iF = np.rint(c_sr*tF).astype(int)
        
        M = iF - i0
        
        max_seconds = max_seconds_dict.get(token_type) # , 0.2) # i don't think this 0.2 default is necessary for the scope of this
        max_samples = int(np.floor(c_sr*max_seconds))
        max_length = min(M, max_samples)
        
        phoneme_array = transcription_to_array(
                        t0, tF, phoneme_onset_times, phoneme_offset_times,
                        phoneme_transcript, max_length, c_sr # makin_sr
                    )
        
        phoneme_sequence = [ph.encode('utf-8') for ph in phoneme_array]
        
        if len(phoneme_sequence) != nsamples:
            if len(phoneme_sequence) > nsamples:
                phoneme_sequence = [phoneme_sequence[i] for i in range(nsamples)]
            else:
                for i in range(nsamples - len(phoneme_sequence)):
                    phoneme_sequence.append(phoneme_sequence[-1])
        
        print('\n------------------------')
        print(f'For sentence {index}: ')
        print(c[0:5,0:5])
        print(f'Latent representation shape: {c.shape} (should be [samples, nchannel])')
        print(text_sequence)
        print(f'Audio sequence: {audio_sequence}')
        print(f'Length of phoneme sequence: {len(phoneme_sequence)}')
        print(phoneme_sequence)
        print('------------------------\n')
        
        example_dicts.append({'ecog_sequence': c, 'text_sequence': text_sequence, 'audio_sequence': [], 'phoneme_sequence': phoneme_sequence,})
    #     break
    # break
    all_example_dict.extend(example_dicts)
    print(len(example_dicts))
    print(len(all_example_dict))
    write_to_Protobuf(tfrecord_path, example_dicts)

print(len(all_example_dict))
